## Подготовка

In [19]:
!pip install nglview --user  

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


In [3]:
import nglview as nv
import requests         
import json             

## Задание 1. 

In [4]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

In [5]:
#   Ключевые слова: caffeine
#   Где они должны быть: заголовок
keyword_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": "caffeine",
        "attribute": "struct.title",
        "operator": "contains_words"
    }
}

my_query["query"]["nodes"].append(keyword_clause)

In [6]:
example_field_search = {
    "type": "terminal",
    "service": "text", 
    "parameters": {
        "value": "caffeine",
        "attribute": "struct.title", 
        "operator": "contains_words" 
                                     
    }
}

In [7]:
# Какое разрешение: не хуже 2 ангстрем

resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.0,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

In [8]:
# Сколько лигандов должно быть в записи

has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 2,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

In [9]:
# Дата публикации записи

date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2020-01-01",
            "to": "2023-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

In [10]:
# Префикс адреса, по которому нужно отослать запрос. 
# Сам запрос должен быть сформирован в виде строки и подан аргументу data

rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'

json_query = json.dumps(my_query) 

search = requests.post(f'{rcsb}', data=json_query) # Отсылаем запрос

In [11]:
search

<Response [200]>

In [12]:
search_result = search.json() # Распаковываем ответ сервера в словарь
search_result

{'query_id': 'b2e2e3c2-11c2-4c06-83e2-50cb69109ad0',
 'result_type': 'entry',
 'total_count': 1,
 'result_set': [{'identifier': '7PBB',
   'score': 1.0,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 5032,
       'original_score': 181.9622344970703,
       'norm_score': 1.0}]}]}]}

In [13]:
best_hit = search_result["result_set"][0] # Лучшая находка
best_hit

{'identifier': '7PBB',
 'score': 1.0,
 'services': [{'service_type': 'text',
   'nodes': [{'node_id': 5032,
     'original_score': 181.9622344970703,
     'norm_score': 1.0}]}]}

## Задание 2. Что нашлось?


Структура (кристалическая) CD73 в комплексе с кофеином в открытой форме.

Публикация от  1 августа 2021 г.  

Разрешение: 1,47 Å

CD73 участвует в пуринергической передаче сигналов, которая влияет на широкий спектр биологических процессов. CD73 гидролизует AMP и является контролем для уровня внеклеточного аденозина.



## Задание 3.

In [14]:
view = nv.show_pdbid('7PBB') 
view

NGLWidget()

In [15]:
from ipywidgets import interact, fixed

In [16]:
my_examples = {
    'Example 1': {
        'description': '''
Поверхность белка покрашена в белый, с непрозрачностью 0.1
Белок в виде rope красного цвета
Боковые радикалы в стержневой модели, покрашенные согласно элементу
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам''',
        'representations': [
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',              
                    'color': '#FFFFFF',
                    'opacity': 0.1
                 }
            },
            {
                'type': 'rope',
                'params': {
                    'sele': 'protein',                 
                    'color': '#FF0000'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',
                    'color' :'element'
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                 }
            },
           
        ],
    },
    'Example 2' : {
        'description': '''
Белок в виде tube, покраска по типу вторичной структуры
Боковые радикалы в стержневой модели, покрашены по гидрофобности
Лиганды показаны линиями, покрашены по элементам
Вода и ионы показаны в виде Ван-дер-Ваальсовых сфер''',
        'representations': [
            {
                'type': 'tube',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'sstruc'
                 }
            },
            {
                'type': 'licorice',
                'params': {
                    'sele': 'sidechain',                 
                    'color': 'hydrophobicity'  
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'ligand C',                
                    'color': 'element'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'water',               
                    'color': 'element'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ion',            
                    'color': 'element', 
                 }
            },
        ],
    },
    'Example 3': {
        'description': '''
Белок в виде cartoon темно-серого цвета
Боковые радикалы в виде линий светло-серого цвета
Боковые радикалы полярных аминокислот в виде hyperball, покрашены по элементам
Лиганды в шаростержневой модели, покрашены по элементам, углероды покрашены в темно-синий''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'darkgrey'  
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'sidechainAttached',               
                    'color': 'lightgrey'  
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'polar and sidechainAttached',               
                    'color': 'element' } 
                 },
                {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'},
                    
                 },
                 { 'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand and _C',               
                    'color': '#00008B'},
                }
        ]
    }
}


In [17]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("3uc8", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 1', 'Example 2', 'Example 3'), va…

NGLWidget()